# Converting the input Video into dataframes for creating datasets for modelling

In [ ]:
# Importing all necessary libraries
import cv2
import os

# Read the video from specified path
cam = cv2.VideoCapture("/content/drive/MyDrive/Exit 2 Main Project/Goal Moment/AMAZING PREMIER LEAGUE GOALS, SCENES & FAN CELEBRATIONS 😍 (online-video-cutter.com) (13).mp4")

try:
	
	# creating a folder named data
	if not os.path.exists('data'):
		os.makedirs('data')

# if not created then raise error
except OSError:
	print ('Error: Creating directory of data')

# frame
currentframe = 0

while(True):
	
	# reading from frame
	ret,frame = cam.read()

	if ret:
		# if video is still left continue creating images
		name = '/content/drive/MyDrive/Exit 2 Main Project/Dataset_for_Testing ' + str(currentframe) + '.jpg'
		print ('Creating...' + name)

		# writing the extracted images
		cv2.imwrite(name, frame)

		# increasing counter so that it will
		# show how many frames are created
		currentframe += 1
	else:
		break

# Release all space and windows once done
cam.release()
cv2.destroyAllWindows()

# Model Creation

In [12]:
#Importing libraries

import numpy as np
from imutils import paths
import os

In [17]:
imagePaths = list(paths.list_images('/content/drive/MyDrive/Exit 2 Main Project/Exit_Test_2/Dataset'))

In [18]:
imagePaths[0]

'/content/drive/MyDrive/Exit 2 Main Project/Exit_Test_2/Dataset/Goal_Moment/Goal_Moment1 0.jpg'

In [19]:
label = imagePaths[0].split(os.path.sep)[-2]
label

'Goal_Moment'

In [20]:
from tensorflow.keras.preprocessing.image import img_to_array
from tensorflow.keras.preprocessing.image import load_img

In [21]:
data = []
labels = []

IMG_SIZE = 224
CHANNELS = 3

for imagePath in imagePaths:
  label = imagePath.split(os.path.sep)[-2]
  image = load_img(imagePath, target_size=(IMG_SIZE, IMG_SIZE))
  image = img_to_array(image)
  image = image/255

  data.append(image)
  labels.append(label)


data = np.array(data, dtype="float32")
labels = np.array(labels)

In [22]:
data.shape

(1392, 224, 224, 3)

In [23]:
labels.shape

(1392,)

In [24]:
labels

array(['Goal_Moment', 'Goal_Moment', 'Goal_Moment', ..., 'Loss_Moments',
       'Loss_Moments', 'Loss_Moments'], dtype='<U12')

In [25]:
np. unique(labels, return_counts=True)

(array(['Goal_Moment', 'Happy_Moment', 'Loss_Moments'], dtype='<U12'),
 array([764, 540,  88]))

In [26]:
# Preprocessing the label by encoding them

from sklearn import preprocessing
le = preprocessing.LabelEncoder()
labels = le.fit_transform(labels)

In [27]:
from tensorflow.keras.utils import to_categorical
labels = to_categorical(labels)

In [28]:
labels

array([[1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       ...,
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.]], dtype=float32)

In [29]:
# Splitting the dataset into train and test

from sklearn.model_selection import train_test_split
(trainX, testX, trainY, testY) = train_test_split(data, labels,	test_size=0.20, stratify=labels, random_state=42)

In [30]:
from tensorflow.keras.applications import ResNet50V2
from tensorflow.keras.layers import Input

In [31]:
feature_extractor_layer = ResNet50V2(weights="imagenet", include_top=False,
	input_tensor=Input(shape=(IMG_SIZE,IMG_SIZE,CHANNELS)))

94668760/94668760 [==============================] - 4s 0us/step


In [32]:
feature_extractor_layer.trainable = False

In [33]:
import tensorflow as tf
from tensorflow.keras import layers
from tensorflow.keras.optimizers import Adam

In [34]:
# Model building

model = tf.keras.Sequential()
model.add(feature_extractor_layer)
model.add(layers.Flatten(name="flatten"))
model.add(layers.Dense(1024, activation='relu', name='hidden_layer'))
model.add(layers.Dropout(0.5))
model.add(layers.Dense(3, activation='softmax', name='output'))

In [35]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 resnet50v2 (Functional)     (None, 7, 7, 2048)        23564800  
                                                                 
 flatten (Flatten)           (None, 100352)            0         
                                                                 
 hidden_layer (Dense)        (None, 1024)              102761472 
                                                                 
 dropout (Dropout)           (None, 1024)              0         
                                                                 
 output (Dense)              (None, 3)                 3075      
                                                                 
Total params: 126,329,347
Trainable params: 102,764,547
Non-trainable params: 23,564,800
_________________________________________________________________


In [36]:
model.compile(
  optimizer=tf.keras.optimizers.Adam(learning_rate=1e-5),
  loss="categorical_crossentropy",
  metrics=["accuracy"])

In [37]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator
aug = ImageDataGenerator(
	rotation_range=20,
	zoom_range=0.15,
	width_shift_range=0.2,
	height_shift_range=0.2,
	shear_range=0.15,
	horizontal_flip=True,
	fill_mode="nearest")

In [38]:
history = model.fit(aug.flow(trainX, trainY),
	                  validation_data=(testX, testY),
	                  epochs=10)

Epoch 1/10
35/35 [==============================] - 30s 484ms/step - loss: 0.8547 - accuracy: 0.7646 - val_loss: 0.0787 - val_accuracy: 0.9606
Epoch 2/10
35/35 [==============================] - 14s 409ms/step - loss: 0.2132 - accuracy: 0.9344 - val_loss: 0.0326 - val_accuracy: 0.9857
Epoch 3/10
35/35 [==============================] - 15s 424ms/step - loss: 0.1129 - accuracy: 0.9623 - val_loss: 0.0231 - val_accuracy: 0.9785
Epoch 4/10
35/35 [==============================] - 14s 409ms/step - loss: 0.0858 - accuracy: 0.9766 - val_loss: 0.0112 - val_accuracy: 0.9928
Epoch 5/10
35/35 [==============================] - 14s 413ms/step - loss: 0.0686 - accuracy: 0.9766 - val_loss: 0.0057 - val_accuracy: 1.0000
Epoch 6/10
35/35 [==============================] - 15s 430ms/step - loss: 0.0676 - accuracy: 0.9784 - val_loss: 0.0163 - val_accuracy: 0.9892
Epoch 7/10
35/35 [==============================] - 14s 409ms/step - loss: 0.0476 - accuracy: 0.9838 - val_loss: 0.0158 - val_accuracy: 0.9928

In [ ]:
testX

In [40]:
from sklearn.metrics import classification_report

predIdxs = model.predict(testX)

9/9 [==============================] - 2s 100ms/step


In [41]:
predIdxs = np.argmax(predIdxs, axis=1)

In [42]:
print(classification_report(testY.argmax(axis=1), predIdxs,target_names=le.classes_))

              precision    recall  f1-score   support

 Goal_Moment       1.00      1.00      1.00       153
Happy_Moment       1.00      1.00      1.00       108
Loss_Moments       1.00      1.00      1.00        18

    accuracy                           1.00       279
   macro avg       1.00      1.00      1.00       279
weighted avg       1.00      1.00      1.00       279



# Converting the video file into dataframe for generating highlight videos

In [ ]:
# Importing all necessary libraries
import cv2
import os

# Read the video from specified path
cam = cv2.VideoCapture("/content/drive/MyDrive/Exit 2 Main Project/Goal Moment/AMAZING PREMIER LEAGUE GOALS, SCENES & FAN CELEBRATIONS 😍 (online-video-cutter.com) (13).mp4")

try:
	
	# creating a folder named data
	if not os.path.exists('data'):
		os.makedirs('data')

# if not created then raise error
except OSError:
	print ('Error: Creating directory of data')

# frame
currentframe = 0

while(True):
	
	# reading from frame
	ret,frame = cam.read()

	if ret:
		# if video is still left continue creating images
		name = '/content/drive/MyDrive/Exit 2 Main Project/Dataset_for_Testing/ ' + str(currentframe) + '.jpg'
		print ('Creating...' + name)

		# writing the extracted images
		cv2.imwrite(name, frame)

		# increasing counter so that it will
		# show how many frames are created
		currentframe += 1
	else:
		break

# Release all space and windows once done
cam.release()
cv2.destroyAllWindows()

# Predicting the class of the input dataframe using the model

In [44]:
imagePaths = list(paths.list_images('/content/drive/MyDrive/Exit 2 Main Project/Dataset_for_Testing'))
imagePaths[0]

'/content/drive/MyDrive/Exit 2 Main Project/Dataset_for_Testing/ 0.jpg'

In [45]:
data = []


IMG_SIZE = 224
CHANNELS = 3

for imagePath in imagePaths:
  
  image = load_img(imagePath, target_size=(IMG_SIZE, IMG_SIZE))
  image = img_to_array(image)
  image = image/255

  data.append(image)
  


data = np.array(data, dtype="float32")


In [46]:
predIdxs = model.predict(testX)

9/9 [==============================] - 1s 94ms/step


In [47]:
predIdxs

array([[9.99999881e-01, 7.91540629e-08, 3.29597433e-10],
       [9.99999285e-01, 7.36590493e-07, 7.69831698e-11],
       [1.39820983e-07, 9.99998927e-01, 9.40940652e-07],
       [2.90006525e-08, 1.00000000e+00, 4.61842717e-11],
       [1.00000000e+00, 1.65423161e-10, 1.76509189e-08],
       [1.11170630e-04, 9.99878049e-01, 1.07035339e-05],
       [1.00000000e+00, 1.63341618e-10, 1.63744032e-10],
       [1.00000000e+00, 3.32149613e-10, 1.55492806e-11],
       [1.00000000e+00, 5.21340660e-08, 1.54926134e-08],
       [3.15480756e-05, 9.99968052e-01, 3.83340932e-07],
       [1.00000000e+00, 5.24480335e-08, 1.55578483e-08],
       [2.65104654e-06, 9.99997258e-01, 1.22112567e-07],
       [1.96343564e-08, 1.00000000e+00, 1.28448558e-08],
       [2.64816435e-06, 9.99985218e-01, 1.21544363e-05],
       [3.43512099e-08, 9.99999642e-01, 4.00735729e-07],
       [9.99999404e-01, 6.44964302e-07, 1.01469189e-11],
       [1.32869616e-07, 9.99999166e-01, 6.88747150e-07],
       [9.99999046e-01, 9.94339

# Video Clipping

In [48]:
pip install imageio-ffmpeg

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 26.9/26.9 MB 27.1 MB/s eta 0:00:00


In [49]:
pip install imageio==2.4.1

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 59.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for imageio: filename=imageio-2.4.1-py3-none-any.whl size=3303886 sha256=a6fae0d724d4e18e24fcefcd5594ab7c25bc053b14f36dfe425e0f61cda5eb49
  Stored in directory: /root/.cache/pip/wheels/be/7b/04/4d8d56f1d503e5c404f0de6018c0cfa592c71588a39b49e002
Successfully built imageio
  Attempting uninstall: imageio
    Found existing installation: imageio 2.9.0
    Uninstalling imageio-2.9.0:
      Successfully uninstalled imageio-2.9.0


In [50]:

# Import everything needed to edit video clips 
from moviepy.editor import *
     
# loading video dsa gfg intro video 
#clip = VideoFileClip("/content/drive/MyDrive/Exit 2 Main Project/AMAZING PREMIER LEAGUE GOALS, SCENES & FAN CELEBRATIONS 😍.mp4") 

clip = VideoFileClip("/content/drive/MyDrive/Exit 2 Main Project/Crazy Open Goal Misses l Unbelievable!.mp4") 
      
      
# getting only first 5 seconds 
clip = clip.subclip(10, 20) 
   
# cutting out some part from the clip
clip = clip.cutout(10, 10)
   
# showing  clip 

clip.ipython_display(width = 360)

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)3088384/45929032 bytes (6.7%)5677056/45929032 bytes (12.4%)8192000/45929032 bytes (17.8%)10362880/45929032 bytes (22.6%)13320192/45929032 bytes (29.0%)15736832/45929032 bytes (34.3%)18595840/45929032 bytes (40.5%)22126592/45929032 bytes (48.2%)25452544/45929032 bytes (55.4%)28631040/45929032 bytes (62.3%)31350784/45929032 bytes (68.3%)34234368/45929032 bytes (74.5%)

100%|█████████▉| 300/301 [00:01<00:00, 253.12it/s]
